In [2]:
# The data for this code is collected from Cruz and Rossi-Hansberg's (2022) online Appendix.

In [ ]:
# Importing needed libaries
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import math 
import h5py
import scipy.io
import csv
import scipy.optimize as optimize
from scipy.optimize import root

from initialize import initialize # Importing the initialize function.

datapath = "/Users/jonebo/Documents/BI/Masteroppgave/Code_EGGW/Data/" # Setting the datapath.

# 0. Loads all the necessary data to run the model

In [344]:
init_re=initialize(8.5,19500,1.6,datapath=datapath) #Callin the initialize function

`ftol` termination condition is satisfied.
Function evaluations 41, initial cost 1.7419e+06, final cost 4.1891e+04, first-order optimality 1.19e-02.


In [345]:
init_re.keys()

dict_keys(['H', 'amen_util0', 'a_norm', 'prod0', 'n', 'lbar', 'λ', 'gamma2', 'η', 'μ', 'ksi', 'α', 'θ', 'Ω', 'trmult_reduced', 'gamma1', 'ν', 'emi0_ff', 'emi_no_ff', 'emi0', 'χ', 'cost_emi_param', 'a0', 'a1', 'a2', 'a3', 'b1', 'b2', 'b3', 'S0', 'S1', 'S2', 'S3', 'S_preind', 'forc_sens', 'forc_noCO2', 'c1', 'c2', 'd1', 'd2', 'temp1', 'temp2', 'temp0_global', 'temp0_local', 'scaler_temp', 'theta_amen_scen', 'theta_prod_scen', 'theta_amen_scen_agri', 'theta_prod_scen_agri', 'name_dam_vect', 'price_clean0_world', 'zeta_clean0', 'zeta_fossil0', 'fossil_share', 'D_vect', 'Africa_vect', 'length_D_vect', 'length_Africa_vect', 'agri_index', 'natal_param', 'natal0', 'natal20', 'name_type_vect', 'name_long_type_vect', 'name_maps_type_vect', 'H0', 'pop0_dens', 'C_vect', 'tCO2_toe', 'fossil0_cell', 'clean0_cell', 'aux_lon', 'aux_lat', 'aux_kron', 'emiCO2_RCP', 'stockCO2_RCP', 'temp_preind', 'temp_global_RCP', 'pop_low95', 'pop_low80', 'pop_med', 'pop_high95', 'pop_high80', 'map0', 'color_darkcyan',

In [346]:
# Loading values in init_re
H, amen_util0, a_norm, prod0, n, lbar, λ, gamma2, η, μ, ksi, α, θ, Ω, trmult_reduced, gamma1, ν, emi0_ff,    \
emi_no_ff, emi0, χ, cost_emi_param, a0, a1, a2, a3, b1, b2, b3, S0, S1, S2, S3, S_preind, forc_sens,         \
forc_noCO2, c1, c2, d1, d2, temp1, temp2, temp0_global, temp0_local, scaler_temp, theta_amen_scen,           \
theta_prod_scen, theta_amen_scen_agri, theta_prod_scen_agri, name_dam_vect, price_clean0_world, zeta_clean0, \
zeta_fossil0, fossil_share, D_vect, Africa_vect, length_D_vect, length_Africa_vect, agri_index, natal_param, \
natal0, natal20, name_type_vect, name_long_type_vect, name_maps_type_vect, H0, pop0_dens, C_vect, tCO2_toe,  \
fossil0_cell, clean0_cell, aux_lon, aux_lat, aux_kron, emiCO2_RCP, stockCO2_RCP, temp_preind, temp_global_RCP, \
pop_low95, pop_low80, pop_med, pop_high95, pop_high80, map0, color_darkcyan, color_olive, color_darkgreen, color_yellowgreen, conv_usd, price_fossil0, price_clean0,ϵ, maxCO2, ind_RCP =init_re.values()

# 1. Estimates natality function, migration costs and energy productivities

In [349]:
#Loading results from the natality function, migration costs and energy productivities. 
results20_d5py = h5py.File(datapath+'Derived/results20_med.mat','r')

l0_model = results20_d5py.get('l0_model')
arr_l0_model=np.array(l0_model).T 

l20 = results20_d5py.get('l20')
arr_l20=np.array(l0_model).T 

realgdp0_model = results20_d5py.get('realgdp0_model')
arr_realgdp0_model=np.array(realgdp0_model).T 

realgdp20 = results20_d5py.get('realgdp20')
arr_realgdp20=np.array(realgdp20).T 

temp20 = results20_d5py.get('temp20')
arr_temp20=np.array(temp20).T 

natal_d5py = h5py.File(datapath+'Derived/natal_migr_Warm_med.mat','r')
coeff_pop_i = natal_d5py.get('coeff_pop_i')
arr_coeff_pop_i=np.array(coeff_pop_i).T 

m2_i = natal_d5py.get('m2_i')
arr_m2_i=np.array(m2_i).T 

upsilon_clean_i = natal_d5py.get('upsilon_clean_i')
arr_upsilon_clean_i=np.array(upsilon_clean_i).T 

upsilon_fossil_i = natal_d5py.get('upsilon_fossil_i')
arr_upsilon_fossil_i=np.array(upsilon_fossil_i).T 

# 2. 2. Runs model backward --baseline estimation  

In [350]:
# Loading the results from backward climate - not relevant for our thesis 
backward_d5py = h5py.File(datapath+'Derived/results_backward_Warm_med.mat','r')
amen_Warm_b = backward_d5py.get('amen_Warm_b')
arr_amen_Warm_b=np.array(amen_Warm_b).T 

clean_Warm_b = backward_d5py.get('clean_Warm_b')
arr_clean_Warm_b=np.array(clean_Warm_b).T 

emiCO2_ff_Warm_b = backward_d5py.get('emiCO2_ff_Warm_b')
arr_emiCO2_ff_Warm_b=np.array(emiCO2_ff_Warm_b).T 

l_Warm_b = backward_d5py.get('l_Warm_b')
arr_l_Warm_b=np.array(l_Warm_b).T

net_births_Warm_b = backward_d5py.get('net_births_Warm_b')
arr_net_births_Warm_b=np.array(net_births_Warm_b).T

price_clean_Warm_b = backward_d5py.get('price_clean_Warm_b')
arr_price_clean_Warm_b=np.array(price_clean_Warm_b).T

price_emi_Warm_b = backward_d5py.get('price_emi_Warm_b')
arr_price_emi_Warm_b=np.array(price_emi_Warm_b).T

prod_Warm_b = backward_d5py.get('prod_Warm_b')
arr_prod_Warm_b=np.array(prod_Warm_b).T

realgdp_Warm_b = backward_d5py.get('realgdp_Warm_b')
arr_realgdp_Warm_b=np.array(realgdp_Warm_b).T

temp_local_Warm_b = backward_d5py.get('temp_local_Warm_b')
arr_temp_local_Warm_b=np.array(temp_local_Warm_b).T

u_Warm_b = backward_d5py.get('u_Warm_b')
arr_u_Warm_b=np.array(u_Warm_b).T
#print(arr_u_Warm_b)

# 3. Runs model forward -- baseline estimation

In [351]:
# Set features of the simulation 
T = 250                           # number of periods
ind_dam = 8                       # damage function level: baseline
name_dam = name_dam_vect[ind_dam] # name of damage function level
ind_exo = 0                       # exogenous temperature and population path
taxCO2 = np.zeros((n,T))          # No taxes
#taxCO2 = 0.5*(np.ones((n,T)))     # Path for carbon taxes
#taxCO2_growth = 1.0363            # Growth rate of taxes for each year. 
#taxCO2 = taxCO2* np.tile(taxCO2_growth**np.arange(T), (n, 1)) # Updating taxCO2. 
subclean = np.zeros((n,T))        # path for clean energy subsidies
abat = np.zeros((n,T))            # path for abatement
val_adap = np.ones((4,1))         # degree of adaptation: baseline
migr_exp = np.ones((2,1))         # border frictions
ind_agri = 0                      # sectoral decomposition
ind_clim = 1

### 3.1 Initialize output variables

In [353]:
# Creating matrixes for relevant output and variables. 
l = np.zeros((n, T))
u = np.zeros((n, T))
prod = np.zeros((n, T))
phi = np.zeros((n, T))
realgdp = np.zeros((n, T))
realincome = np.zeros((n, T))
realgdp_w = np.zeros((T, 1))
price_fossil = np.zeros((n, T))
price_clean = np.zeros((n, T))
price_energy = np.zeros((n, T))
price_energy_tilde = np.zeros((n, T))
varphi = np.zeros((n, T))
zeta_fossil = np.zeros((n, T))
zeta_clean = np.zeros((n, T))
clean = np.zeros((n, T))
cumCO2_ff = np.zeros((T, 1))
emiCO2_ff_abat = np.zeros((n, T))
emiCO2_total = np.zeros((T, 1))
stockCO2_layers = np.zeros((4, T))
forc = np.zeros((T, 1))
temp_layers = np.zeros((2, T))
temp_local = np.zeros((n, T))
amen = np.zeros((n, T))
net_births = np.zeros((n, T))

if ind_exo == 0:                         # endogenous CO2 emissions, temperature and population
    emiCO2_ff = np.zeros((n, T))
    temp_global = np.zeros((T, 1))
    lbar_time = np.zeros((T+1, 1))
    
elif ind_exo == 1:                       # exogenous CO2 emissions, temperature and population
    if ind_clim == 1:
        data_Warm = np.load(datapath+'derived/results_forward_Warm_' + name_dam_vect[ind_dam] + '.npz')
        emiCO2_ff = data_Warm['emiCO2_ff_Warm']
        temp_global = data_Warm['temp_global_Warm']
        l_Warm = data_Warm['l_Warm']
        lbar_time = np.sum(l_Warm * np.tile(H, (T, 1)), axis=0)
    else:
        data_noWarm = np.load(datapath+'derived/results_forward_noWarm.npz')
        emiCO2_ff = data_noWarm['emiCO2_ff_noWarm']
        temp_global = data_noWarm['temp_global_noWarm']
        l_noWarm = data_noWarm['l_noWarm']
        lbar_time = np.sum(l_noWarm * np.tile(H, (T, 1)), axis=0)
elif ind_exo == 2:
    lbar_time = np.tile(lbar, (T+1, 1)).T
elif ind_exo == 3:
    lbar_time = np.tile(lbar, (T+1, 1)).T
    if ind_clim == 1:
        data_Warm = np.load(datapath+'derived/results_forward_Warm_' + name_dam_vect[ind_dam] + '.npz')
        emiCO2_ff = data_Warm['emiCO2_ff_Warm']
        temp_global = data_Warm['temp_global_Warm']
    else:
        data_noWarm = np.load(datapath+'derived/results_forward_noWarm.npz')
        emiCO2_ff = data_noWarm['emiCO2_ff_noWarm']
        temp_global = data_noWarm['temp_global_noWarm']
        


### 3.2 Initialize parameters and variables of initial period 

In [354]:
# Read parameters
data_natal = h5py.File(datapath+'derived/natal_migr_Warm_med.mat','r')

m2 = np.array(data_natal.get('m2_i')).T 
m2 = m2.reshape(-1)
coeff_pop = np.array(data_natal.get('coeff_pop_i')).T 
coeff_pop = coeff_pop.reshape(-1)
upsilon_fossil = data_natal['upsilon_fossil_i'][0, 0]
upsilon_clean = data_natal['upsilon_clean_i'][0, 0]


data_20 = h5py.File(datapath+'derived/results20_med.mat','r')
l0_model = data_20['l0_model'][:].T 
l0_model = l0_model.reshape(-1)
realgdp0 = data_20['realgdp0_model'][:].T
realgdp0 = realgdp0.reshape(-1)
realgdp0_w = np.sum(realgdp0 * l0_model * H) / lbar

# Adjust migration costs
if migr_exp[0] != 1:
    length_border_vect = length_D_vect
    border_vect = D_vect
    border_migr_exp = migr_exp[0]
elif migr_exp[1] != 1:
    length_border_vect = length_Africa_vect
    border_vect = Africa_vect
    border_migr_exp = migr_exp[1]
if np.sum(np.abs(migr_exp - 1)) != 0:
    n2 = np.zeros(n)
    for i in range(length_border_vect):
        n2_aux = np.sum(m2[border_vect==i] * l0_model[border_vect==i] * H[border_vect==i]) / \
                  np.sum(l0_model[border_vect==i] * H[border_vect==i])
        n2[border_vect==i] = n2_aux
    m2 = (m2 / n2)
    m2 = m2 / np.min(m2)
    n2 = n2 / np.min(n2)
    m2 = m2 * (n2**border_migr_exp)


# Update adaptation parameters
trmult_reduced_aux = trmult_reduced ** val_adap[0]
m2_aux = m2 ** val_adap[1]
gamma1_aux = gamma1 * val_adap[2]
Omega_aux = Ω * val_adap[3]

# Update productivity and amenities
avgprod = np.mean(prod0)
const_phi = ((gamma1_aux / ksi) / (ν * (μ + gamma1_aux / ksi)))**(1/ksi)
const_energy = (1 - χ) * μ / (μ + gamma1_aux / ksi)

phi0 = const_phi * l0_model**(1/ksi)
prod[:,0] = η * prod0**gamma2 * avgprod**(1-gamma2) * phi0**(gamma1_aux*θ) 
amen[:,0] = a_norm

# Set CO2 stock, forcing and temperature
if ind_exo == 0 or ind_exo == 2:
    stockCO2_layers[0,0] = S0 + a0*emi0
    stockCO2_layers[1,0] = (np.exp(-1/b1))*S1 + a1*emi0
    stockCO2_layers[2,0] = (np.exp(-1/b2))*S2 + a2*emi0
    stockCO2_layers[3,0] = (np.exp(-1/b3))*S3 + a3*emi0

    forc[0] = forc_sens*np.log(np.sum(stockCO2_layers[:,0])/S_preind)/np.log(2) + forc_noCO2[0]

    temp_layers[0,0] = (np.exp(-1/d1))*temp1 + (c1/d1)*forc[0]
    temp_layers[1,0] = (np.exp(-1/d2))*temp2 + (c2/d2)*forc[0]

    temp_global[0] = np.sum(temp_layers[:,0])
    
temp_local[:,0] = temp0_local.flatten() + scaler_temp.squeeze()*(temp_global[0]-temp0_global)
temp_local_aux = temp_local[:,0]
Delta_temp = temp_local[:,0] - temp0_local.flatten()  

# Set damage function level by confidence interval
if ind_clim != 0:
    if ind_agri == 0:
        theta_amen_min = theta_amen_scen[0, ind_dam]
        theta_amen_max = theta_amen_scen[1, ind_dam]
        theta_amen_center = theta_amen_scen[2, ind_dam]
        theta_amen_steep = theta_amen_scen[3, ind_dam]
        theta_amen_temp = lambda temp: theta_amen_min + (theta_amen_max - theta_amen_min) / (1 + np.exp(theta_amen_steep * (temp - theta_amen_center)))
        
        theta_prod_min = theta_prod_scen[0, ind_dam]
        theta_prod_max = theta_prod_scen[1, ind_dam]
        theta_prod_center = theta_prod_scen[2, ind_dam]
        theta_prod_steep = theta_prod_scen[3, ind_dam]
        theta_prod_temp = lambda temp: theta_prod_min + (theta_prod_max - theta_prod_min) / (1 + np.exp(theta_prod_steep * (temp - theta_prod_center)))
    else:
        theta_amen_min = theta_amen_scen_agri[0, :]
        theta_amen_max = theta_amen_scen_agri[1, :]
        theta_amen_center = theta_amen_scen_agri[2, :]
        theta_amen_steep = theta_amen_scen_agri[3, :]
        theta_amen_temp = lambda temp, agri_index: theta_amen_min[agri_index] + (theta_amen_max[agri_index] - theta_amen_min[agri_index]) / (1 + np.exp(theta_amen_steep[agri_index] * (temp - theta_amen_center[agri_index])))
        
        theta_prod_min = theta_prod_scen_agri[0, :]
        theta_prod_max = theta_prod_scen_agri[1, :]
        theta_prod_center = theta_prod_scen_agri[2, :]
        theta_prod_steep = theta_prod_scen_agri[3, :]
        theta_prod_temp = lambda temp, agri_index: theta_prod_min[agri_index] + (theta_prod_max[agri_index] - theta_prod_min[agri_index]) / (1 + np.exp(theta_prod_steep[agri_index] * (temp - theta_prod_center[agri_index])))

# Set damage function sources: amenities or productivities
if ind_clim == 1:      # damages on both amenities and productivities
    if ind_agri == 0:
        amen[:,0] = (1 + theta_amen_temp(temp_local_aux) * Delta_temp) * amen[:,0]
        prod[:,0] = (1 + theta_prod_temp(temp_local_aux) * Delta_temp) * prod[:,0]
    else:
        amen[:,0] = (1 + theta_amen_temp(temp_local_aux,agri_index) * Delta_temp) * amen[:,0]
        prod[:,0] = (1 + theta_prod_temp(temp_local_aux,agri_index) * Delta_temp) * prod[:,0]
elif ind_clim == 2:   # damages only on amenities
    if ind_agri == 0:
        amen[:,0] = (1 + theta_amen_temp(temp_local_aux) * Delta_temp) * amen[:,0]
    else:
        amen[:,0] = (1 + theta_amen_temp(temp_local_aux,agri_index) * Delta_temp) * amen[:,0]
elif ind_clim == 3:   # damages only on productivities
    if ind_agri == 0:
        prod[:,0] = (1 + theta_prod_temp(temp_local_aux) * Delta_temp) * prod[:,0]
    else:
        prod[:,0] = (1 + theta_prod_temp(temp_local_aux,agri_index) * Delta_temp) * prod[:,0]


# 3.2.1 Natality function

In [355]:
# Creating the natality function. 
def natal_fct(logrealgdp, temp, logrealgdp_w, coeff_pop_d):
    data_20 = h5py.File(datapath+'derived/results20_med.mat','r')
    l0_model = data_20['l0_model'][:].T 
    l0_model = l0_model.reshape(-1)
    realgdp0 = data_20['realgdp0_model'][:].T
    realgdp0 = realgdp0.reshape(-1)
    l20 = data_20['l20'][:].T
    l20 = l20.reshape(-1)
    realgdp20 = data_20['realgdp20'][:].T
    realgdp20 = realgdp20.reshape(-1)
    temp20 = data_20['temp20'][:].T
    temp20 = temp20.reshape(-1)
    logrealgdp0 = np.log(realgdp0)
    realgdp0_w = np.sum(realgdp0 * l0_model * H) / lbar
    logrealgdp0_w = np.log(realgdp0_w)
    logrealgdp20 = np.log(realgdp20)
    logrealgdp20_w = np.log(np.sum(realgdp20 * l20 * H) / np.sum(l20 * H))
    pop0_sh = l0_model * H / lbar
    pop20_sh = l20 * H / np.sum(l20 * H)
    
    # Read numerical restrictions on natality functions
    b0y_max, b1y_min, b1y_max, b2y_min, b2y_max, b2T_max, bsy_min, bsy_max, bsT_min, bsT_max = natal_param

    logi_b2T_fct = lambda x: b2T_max / (1 + np.exp(-x))
    logi_b0y_fct = lambda x: b0y_max / (1 + np.exp(-x))
    logi_b1y_fct = lambda x: b1y_min + (b1y_max - b1y_min) / (1 + np.exp(-x))
    logi_b2y_fct = lambda x: b2y_min + (b2y_max - b2y_min) / (1 + np.exp(-x))
    logi_bsy_fct = lambda x: bsy_min + (bsy_max - bsy_min) / (1 + np.exp(-x))
    logi_bsT_fct = lambda x: bsT_min + (bsT_max - bsT_min) / (1 + np.exp(-x))
    natal_fct_logrealgdp = lambda logrealgdp, coeff_pop: \
    (logi_b0y_fct(coeff_pop_d[0]) + \
    (logi_b2y_fct(coeff_pop_d[3])-logi_b0y_fct(coeff_pop_d[0])) * \
    np.exp(-logi_b1y_fct(coeff_pop_d[1]) * np.square(logrealgdp - logi_bsy_fct(coeff_pop_d[4]))) * \
    (logrealgdp < logi_bsy_fct(coeff_pop[4]))) + \
    (0 + \
    (logi_b2y_fct(coeff_pop_d[3])-0) * \
    np.exp(-np.exp(coeff_pop_d[2]) * np.square(logrealgdp - logi_bsy_fct(coeff_pop_d[4]))) * \
    (logrealgdp >= logi_bsy_fct(coeff_pop_d[4])))

    # Call the function 
    result = natal_fct_logrealgdp(logrealgdp, coeff_pop_d)

    # Define b0T, equation (30)
    b0T = 2 * natal0 - logi_b2T_fct(coeff_pop_d[6]) * np.sum(np.exp(-np.exp(coeff_pop_d[5]) * (temp0_local - logi_bsT_fct(coeff_pop_d[7])) ** 2) * pop0_sh) - 2 * np.sum(natal_fct_logrealgdp(logrealgdp0, coeff_pop_d) * pop0_sh)

    # Construct bw, equation (32) 
    term1 = b0T + np.sum(logi_b2T_fct(coeff_pop_d[6]) * np.exp(-np.exp(coeff_pop_d[5]) * (temp20 - logi_bsT_fct(coeff_pop_d[7])) ** 2) * pop20_sh)
    term2 = natal20 - np.sum(natal_fct_logrealgdp(logrealgdp20, coeff_pop_d) * pop20_sh)
    term3 = logrealgdp20_w - logrealgdp0_w
    bw = np.log(-1 + (term1 * np.ones_like(term2)) / term2) / term3

    # Construct numerator of temperature component of natality rate function
    natal_fct_temp_num = b0T + logi_b2T_fct(coeff_pop[6]) * np.exp(-np.exp(coeff_pop[5]) * (temp_local_aux - logi_bsT_fct(coeff_pop[7])) ** 2)

    # Construct denominator of temperature component of natality rate function,
    natal_fct_temp_denom = (1 + np.exp(bw * (logrealgdp_w - logrealgdp0_w)))

    # Construct natality functions
    natal_fct_val = np.real(natal_fct_temp_num / natal_fct_temp_denom + \
                            natal_fct_logrealgdp(logrealgdp, coeff_pop_d))
    return natal_fct_val

In [356]:
logrealgdp0 = np.log(realgdp0)
logrealgdp0_w = np.log(realgdp0_w)
if ind_exo == 0:
    net_births0 = natal_fct(logrealgdp0, temp0_local, logrealgdp0_w, coeff_pop)
    #print('net_births0',net_births0)
    pop_prev = H * l0_model * (1 + net_births0)
    #print('pop_prev', pop_prev)
    lbar_time[0] = round(sum(pop_prev))
    #print('lbar_time', lbar_time[0])

net_births0 [0.00600261 0.0061086  0.00618025 ... 0.01366469 0.01379883 0.01402889]
pop_prev [ 247.57686888   33.99282728  451.18803032 ... 7713.40894837 4983.23742718
  597.67123941]
lbar_time [5.99320463e+09]


In [357]:
# Define function for extraction cost function
def costCO2_fct(cumCO2):
    return cost_emi_param[0]/(cost_emi_param[1] + np.exp(-cost_emi_param[2]*(cumCO2-cost_emi_param[3]))) - \
        cost_emi_param[4]*(cost_emi_param[5]/(cumCO2-cost_emi_param[5]))**cost_emi_param[6]


In [358]:
# Precompute auxiliary variables
denom = 1 + 2 * θ
squ = (α - 1 + (λ + gamma1_aux / ksi - (1 - μ)) * θ)  # term in square brackets of flat_R and flat_L

flatL = λ - squ / denom
flatR = 1 - λ * θ + (1 + θ) * squ / denom
flat = flatR - θ * flatL

exp_uhatL = flatL / Omega_aux + (1 + θ) / denom
exp_uhatR = flatR / Omega_aux - θ**2 / denom


In [359]:
FL_H_m2 = (np.power(H, (flatL-1/denom)/exp_uhatL) * np.power(m2_aux, flatL/(Omega_aux*exp_uhatL))) #Removed reshape
FR_H_m2 = (np.power(H, -flatR+θ/denom) * np.power(m2_aux, -flatR/Omega_aux)) #Removed reshape


In [360]:
# Set guesses for the simulation.
uhat_i = np.ones(n)                          # guess for uhat
if ind_exo == 0 or ind_exo == 2:
    emi_ff_i = emi0_ff                      # guess for global CO2 emissions
    
realgdp_growth_i = 1.017                    # guess for global realgdp growth

uhat_i = uhat_i

In [361]:
# Set numerical parameters
updatee = 1                                  # speed of update when iterating over CO2 emissions
updater = 1

tol = 1e-2                                   # tolerance for error when iterating over uhat
tol_e = 1e-2                                 # tolerance for error when iterating over CO2 emissions
tol_realgdp = 1e-2


### 3.3 Simulate the model

In [364]:
i_1st = 0
i_2nd = 0
i_3rd = 0

In [365]:
# Creating dictionary for input variables
my_dict = {
    'zeta_fossil0': zeta_fossil0,
    'zeta_clean0': zeta_clean0,
    'realgdp0_w': realgdp0_w,
    'emi0_ff': emi0_ff,
    'zeta_fossil': zeta_fossil,
    'zeta_clean': zeta_clean,
    'realgdp_w_prev': realgdp_w,
    'cumCO2_ff': cumCO2_ff,
    'H': H,
    'cost_emi_param': cost_emi_param,
    'costCO2_fct': costCO2_fct,
    'amen': amen,
    'θ': θ,
    'denom': denom,
    'exp_uhatL': exp_uhatL,
    'prod': prod,
    'FL_H_m2': FL_H_m2,
    'FR_H_m2': FR_H_m2,
    'tol_realgdp': tol_realgdp,
    'i_1st': i_1st,
    'i_2nd': i_2nd,
    'i_3rd': i_3rd, 
    'tol_e': tol_e,
    'price_clean0_world': price_clean0_world,
    'fossil_share': fossil_share,
    'taxCO2': taxCO2, 
    'ϵ': ϵ,
    'subclean': subclean,
    'μ': μ,
    'χ': χ,
    'gamma1_aux': gamma1_aux,
    'ksi': ksi,
    'uhat_i': uhat_i,
    'exp_uhatR': exp_uhatR,
    'trmult_reduced_aux': trmult_reduced_aux,
    'Omega_aux': Omega_aux,
    'm2_aux': m2_aux,
    'lbar_time': lbar_time,
    'const_phi': const_phi, 
    'flat': flat,
    'u': u,
    'λ': λ,
    'η': η,
    'gamma2': gamma2,
    'avgprod': avgprod,
    'const_energy': const_energy,
    'ind_exo': ind_exo,
    'T': T,
    'abat': abat,
    'emiCO2_ff': emiCO2_ff,
    'emi_no_ff': emi_no_ff,
    'updatee': updatee, 
    'emi_ff_i': emi_ff_i,
    'realgdp_growth_i': realgdp_growth_i,
    'updater': updater,
    'stockCO2_layers': stockCO2_layers,
    'a0': a0,
    'b1': b1,
    'a1': a1,
    'a2': a2,
    'a3': a3,
    'b2': b2,
    'b3': b3, 
    'forc_sens': forc_sens,
    'S_preind': S_preind,
    'forc_noCO2': forc_noCO2, 
    'temp_layers': temp_layers, 
    'c1': c1,
    'c2': c2,
    'd1': d1,
    'd2': d2,
    'temp0_global': temp0_global, 
    'temp0_local': temp0_local, 
    'scaler_temp': scaler_temp, 
    'ind_clim': ind_clim,
    'ind_agri': ind_agri,
    'theta_amen_temp': theta_amen_temp,
    'temp_local_aux': temp_local_aux,
    'theta_prod_temp': theta_prod_temp,
    'agri_index': agri_index, 
    'natal_fct': natal_fct,
    'coeff_pop': coeff_pop,
}

In [366]:
# Defining a function for the simulation
def my_function(my_dict):
    zeta_fossil0 = my_dict['zeta_fossil0']
    zeta_clean0 = my_dict['zeta_clean0']
    realgdp0_w = my_dict['realgdp0_w']
    emi0_ff = my_dict['emi0_ff']
    zeta_fossil = my_dict['zeta_fossil']
    zeta_clean = my_dict['zeta_clean']
    realgdp_w_prev = my_dict['realgdp_w_prev']
    cumCO2_ff = my_dict['cumCO2_ff']
    H = my_dict['H']
    cost_emi_param = my_dict['cost_emi_param']
    costCO2_fct = my_dict['costCO2_fct']
    amen = my_dict['amen']
    θ = my_dict['θ']
    denom = my_dict['denom']
    exp_uhatL = my_dict['exp_uhatL']
    prod = my_dict['prod']
    FL_H_m2 = my_dict['FL_H_m2']
    FR_H_m2 = my_dict['FR_H_m2']
    tol_realgdp = my_dict['tol_realgdp']
    i_1st = my_dict['i_1st']
    i_2nd = my_dict['i_2nd']
    i_3rd = my_dict['i_3rd']
    tol_e = my_dict['tol_e']
    price_clean0_world = my_dict['price_clean0_world']
    fossil_share = my_dict['fossil_share']
    taxCO2 = my_dict['taxCO2']
    ϵ = my_dict['ϵ']
    subclean = my_dict['subclean']
    μ = my_dict['μ']
    χ = my_dict['χ']
    gamma1_aux = my_dict['gamma1_aux']
    ksi = my_dict['ksi']
    uhat_i = my_dict['uhat_i']
    exp_uhatR = my_dict['exp_uhatR']
    trmult_reduced_aux = my_dict['trmult_reduced_aux']
    Omega_aux = my_dict['Omega_aux']
    m2_aux = my_dict['m2_aux']
    lbar_time = my_dict['lbar_time']
    const_phi = my_dict['const_phi']
    flat = my_dict['flat']
    u = my_dict['u']
    λ = my_dict['λ']
    η = my_dict['η']
    gamma2 = my_dict['gamma2']
    avgprod = my_dict['avgprod']
    const_energy = my_dict['const_energy']
    ind_exo = my_dict['ind_exo']
    T = my_dict['T']
    abat = my_dict['abat']
    emiCO2_ff = my_dict['emiCO2_ff']
    emi_no_ff = my_dict['emi_no_ff']
    updatee = my_dict['updatee']
    emi_ff_i = my_dict['emi_ff_i']
    realgdp_growth_i = my_dict['realgdp_growth_i']
    updater = my_dict['updater']
    stockCO2_layers = my_dict['stockCO2_layers']
    a0 = my_dict['a0']
    b1 = my_dict['b1']
    a1 = my_dict['a1']
    a2 = my_dict['a2']
    a3 = my_dict['a3']
    b2 = my_dict['b2']
    b3 = my_dict['b3']
    forc_sens = my_dict['forc_sens']
    S_preind = my_dict['S_preind']
    forc_noCO2 = my_dict['forc_noCO2']
    temp_layers = my_dict['temp_layers']
    c1 = my_dict['c1']
    c2 = my_dict['c2']
    d1 = my_dict['d1']
    d2 = my_dict['d2']
    temp0_local = my_dict['temp0_local']
    temp0_global = my_dict['temp0_global']
    scaler_temp = my_dict['scaler_temp']
    ind_clim = my_dict['ind_clim']
    ind_agri = my_dict['ind_agri']
    theta_amen_temp = my_dict['theta_amen_temp']
    temp_local_aux = my_dict['temp_local_aux']
    theta_prod_temp = my_dict['theta_prod_temp']
    agri_index = my_dict['agri_index']
    natal_fct = my_dict['natal_fct']
    coeff_pop = my_dict['coeff_pop']

    for t in range(T):
        if t == 0:
            zeta_fossil_prev = zeta_fossil0 # Very, very small difference from MatLab
            zeta_clean_prev = zeta_clean0 #Same as MatLab
            realgdp_w_prev = realgdp0_w # Same as MatLab
            cumCO2_ff[t] = emi0_ff # Same as matlab
            #print('zeta_fossil_prev', zeta_fossil_prev) #Very small difference from MatLab.
            #print('zeta_clean_prev', zeta_clean_prev)#Correct
            #print('realgdp_w_prev', realgdp_w_prev)#Correct
            #print('cumCO2CO2_ff[t]', cumCO2_ff[t]) #Correct
        else:
            zeta_fossil_prev = zeta_fossil[:, t-1]
            zeta_clean_prev = zeta_clean[:, t-1]
            realgdp_w_prev = realgdp_w[t-1]
            cumCO2_ff_aux = cumCO2_ff[t-1] + sum(emiCO2_ff[:, t-1] * H)
            ind_cumCO2 = (cumCO2_ff_aux >= cost_emi_param[5] - 0.5)
            if ind_cumCO2:
                cumCO2_ff_aux = cost_emi_param[5] - 0.5
            cumCO2_ff[t] = cumCO2_ff_aux

        # Compute extraction cost
        costCO2_avg_i = costCO2_fct(cumCO2_ff[t]) 
        #print('costCO2_avg_i', costCO2_avg_i) #We get 126.4502 in python and 126.4915 in MatLab

        # Pre-compute auxiliary variables to equation (70)  
        FL_aux = amen[:,t]**((1+θ)/(denom*exp_uhatL)) * \
            prod[:,t]**(1/(denom*exp_uhatL)) * \
            FL_H_m2  # outside the integral

        #print('FL_aux', FL_aux) #Small difference in the value, i.e: 186719.89 (Python) vs. 186686,6
        #print(FL_aux.shape) #Same shape when using "amen[:, 0:1]". 

        FR_aux = amen[:,t]**(θ**2/denom) * \
            prod[:,t]**((1+θ)/denom) * \
            FR_H_m2  # inside the integral 

        #print('FR_aux', FR_aux) #Difference in value here as well.
        #print(FR_aux.shape) #Same shape when using "amen[:,0:1]". 

        error_realgdp = 1 + tol_realgdp
        i_1st = 0
        while error_realgdp > tol_realgdp:
        #for i in range(1):
            i_1st += 1

            # Update energy productivity, equation (10)
            zeta_fossil[:,t] = zeta_fossil_prev*(realgdp_growth_i)**(upsilon_fossil)
            zeta_clean[:,t] = zeta_clean_prev*(realgdp_growth_i)**(upsilon_clean)
            #print('zeta_fossil[:,t]', zeta_fossil[:,t]) #Small difference in the values. 
            #print(zeta_fossil[:,t].shape) #Is this shape correct?
            #print('zeta_clean', zeta_clean[:,t]) #This seems to be correct.

            error_e = 1 + tol_e
            #print(error_e)
            i_2nd = 0
            while error_e > tol_e:
                i_2nd += 1
            #for j in range(1):
                #print('j', j)
                #print('error_e', error_e)
                # Construct energy price, equations (8), (40), (42) and (46)
                price_fossil[:,t] = costCO2_avg_i/zeta_fossil[:,t]
                price_clean[:,t] = price_clean0_world/zeta_clean[:,t]
                price_energy[:,t] = \
                    (fossil_share**ϵ*(1+taxCO2[:,t])**(1-ϵ)*price_fossil[:,t]**(1-ϵ) + \
                    (1-fossil_share)**ϵ*(1-subclean[:,t])**(1-ϵ)*price_clean[:,t]**(1-ϵ))**(1/(1-ϵ))
                #price_energy[:,t] = price_energy[:, t] #Removed reshape and changed from price_energy[:,t:t+1]
                price_energy_tilde[:,t] = \
                    (fossil_share**ϵ*(1+taxCO2[:,t])**(-ϵ)*price_fossil[:,t]**(1-ϵ) + \
                    (1-fossil_share)**ϵ*(1-subclean[:,t])**(-ϵ)*price_clean[:,t]**(1-ϵ))**(1/(1-ϵ))
                varphi[:,t] = (μ*χ + gamma1_aux/ksi + μ*(1-χ)*(price_energy_tilde[:,t]/price_energy[:,t])**(1-ϵ))/\
                    (μ+gamma1_aux/ksi)
                #varphi[:,t] = varphi[:, t] #removed reshape and changed from varphi[:,t:t+1]
                #print('varphi', varphi[:,t])#All of these checked, matches with the first column of the different variables (price_fossil etc) in MatLab
                #print(varphi[:,t].shape)

                # Precompute auxiliary variables to equation (70)
                #FL = FL_aux * np.power(price_energy[:,t], (-θ*μ*(1-χ)/(denom*exp_uhatL))) * \
                    #np.power(varphi[:,t], (θ*(μ+gamma1_aux/ksi)/(denom*exp_uhatL))) # outside the integral

                FL = FL_aux * \
                    price_energy[:,t]**(-θ*μ*(1-χ)/(denom*exp_uhatL)) * \
                    varphi[:,t]**(θ*(μ+gamma1_aux/ksi)/(denom*exp_uhatL)) # outside the integral
                #print('FL', FL) #Seems correct
                #print(FL.shape)
                FR = FR_aux * \
                    price_energy[:,t]**(-θ*(1+θ)*μ*(1-χ)/denom) * \
                    varphi[:,t]**(θ*(1+θ)*(μ+gamma1_aux/ksi)/denom) # inside the integral
                #print('FR', FR) #There are some small differences in this value. 
                #print(FR.shape)

                # Iterate uhat, equation (70)
                error = tol + 1
                #print('tol', tol)

                i_3rd = 0
                while error >= tol:
                    i_3rd += 1
                #for k in range(1):
                    #print('k', k)
                    #integral = FR * uhat_i**exp_uhatR
                    integral = FR * np.power(uhat_i, exp_uhatR)
                    rhs = np.matmul(trmult_reduced_aux, integral) 
                    uhat_f = FL * rhs**(1/(θ*exp_uhatL))
                    error = np.sum((uhat_i - uhat_f)**2)
                    uhat_i = uhat_f.copy()
                    #print('error',error)

                    # Solve for population, equation (3), and scale it to add up to lbar_time(t)
                # Solve for population, equation (3), and scale it to add up to lbar_time(t)
                l[:,t] = H**(-1) * uhat_i**(1/Omega_aux) * m2_aux**(-1/Omega_aux)
                #print('l', l[:,t])
                l[:,t] = l[:,t] / np.sum(H*l[:,t]) * lbar_time[t]
                #print('l1', l[:,t])

                # Calculate innovation, equations (45) and (47)
                phi[:,t] = const_phi * (l[:,t]/varphi[:,t])**(1/ksi)
                #print('phi', phi[:,t])

                # Retrieve utility, equation (71)
                u[:,t] = uhat_i * \
                    (lbar_time[t]/np.sum(uhat_i**(1/Omega_aux)*m2_aux**(-1/Omega_aux)))**(flat/θ)
                #print('u[:,t]', u[:,t])

                # Calculate real income and real GDP per capita, equation (4) 
                realincome[:,t] = u[:,t] / amen[:,t] * l[:,t]**λ
                #print('realincome', realincome[:,t])
                realgdp[:,t] = (1 + (μ+gamma1_aux/ksi)*(varphi[:,t]-1)) * realincome[:,t]
                #print('realgdp[:,t]', realgdp[:,t])
                realgdp_w[t] = sum(realgdp[:,t] * H * l[:,t]) / sum(H * l[:,t])
                #print('realgdp_w[t]', realgdp_w[t])

                # Update productivity, equation (6)
                if t < T-1:
                    avgprod = np.mean(prod[:,t])
                    #print('avgprod', avgprod)
                    prod[:,t+1] = η * prod[:,t]**gamma2 * avgprod**(1-gamma2) * phi[:,t]**(gamma1_aux*θ)
                    #print('prod[:,t+1]', prod[:,t+1])

                # Calculate clean energy use, equation (49)
                clean[:,t] = const_energy * (1 / varphi[:,t]) * (l[:,t] / price_energy[:,t]) * \
                    ((1-fossil_share) * price_energy[:,t] / ((1-subclean[:,t]) * price_clean[:,t]))**ϵ
                #print('clean[:,t]', clean[:,t])

                # Calculate CO2 emissions, equation (48)
                if ind_exo == 0 or ind_exo == 2:
                    emiCO2_ff[:,t] = const_energy * (1 / varphi[:,t]) * (l[:,t] / price_energy[:,t]) * \
                        (fossil_share * price_energy[:,t] / ((1+taxCO2[:,t]) * price_fossil[:,t]))**ϵ
                    #print('emiCO2_ff[:,t]', emiCO2_ff[:,t])

                # Update CO2 emissions by abatement 
                emiCO2_ff_abat[:,t] = (1 - abat[:,t]) * emiCO2_ff[:,t]
                #print('emiCO2_ff_abat[:,t]', emiCO2_ff_abat[:,t])
                emi_ff_f = np.sum(emiCO2_ff[:,t] * H)
                #print('emi_ff_f', emi_ff_f)
                emi_ff_f_abat = np.sum(emiCO2_ff_abat[:,t] * H)
                #print('emi_ff_f_abat', emi_ff_f_abat)
                emiCO2_total[t] = emi_ff_f_abat + emi_no_ff[t]
                #print('emiCO2_total[t]', emiCO2_total[t])

                # Compare global CO2 emissions
                if ind_exo == 0 or ind_exo == 2:
                    error_e = np.abs(emi_ff_f - emi_ff_i)
                    #print('error_e', error_e)
                    emi_ff_i = updatee * emi_ff_f + (1 - updatee) * emi_ff_i
                    #print('emi_ff_i', emi_ff_i)
                    costCO2_avg_i = np.mean(costCO2_fct(cumCO2_ff[t] + np.linspace(0,emi_ff_i,100)))
                    #print('costCO2_avg_i', costCO2_avg_i)
                else:
                    error_e = 0

                #display(f"t = {t}; error_e = {error_e}; No.iter 3rd loop = {i_3rd}")

            # Compare growth rate realgdp
            realgdp_growth_f = realgdp_w[t] / realgdp_w_prev
            #print('realgdp_growth_f', realgdp_growth_f)
            error_realgdp = abs(realgdp_growth_f - realgdp_growth_i)
            #print('error_realgdp', error_realgdp)
            realgdp_growth_i = updater * realgdp_growth_f + (1 - updater) * realgdp_growth_i
            #print('realgdp_growth_i', realgdp_growth_i)
            #display(f"t = {t}; error_realgdp = {error_realgdp}; error_e = {error_e}; No.iter 2nd loop = {i_2nd}")


        # Set growth rate of previous period
        realgdp_growth_i = realgdp_growth_f
        #print('realgdp_growth_i',realgdp_growth_i)

        if t<T-1:
            # Update CO2 stock, forcing and temperature, equations (9), (17) and (35)-(37)
            if ind_exo == 0 or ind_exo == 2:
                stockCO2_layers[0,t+1] = stockCO2_layers[0,t] + a0*emiCO2_total[t]
                #print('stockCO2_layers[0,t+1]', stockCO2_layers[0,t+1])
                stockCO2_layers[1,t+1] = np.exp(-1/b1)*stockCO2_layers[1,t] + a1*emiCO2_total[t]
                #print('stockCO2_layers[1,t+1]',stockCO2_layers[1,t+1])
                stockCO2_layers[2,t+1] = np.exp(-1/b2)*stockCO2_layers[2,t] + a2*emiCO2_total[t]
                #print('stockCO2_layers[2,t+1]', stockCO2_layers[2,t+1])
                stockCO2_layers[3,t+1] = np.exp(-1/b3)*stockCO2_layers[3,t] + a3*emiCO2_total[t]
                #print('stockCO2_layers[3,t+1]', stockCO2_layers[3,t+1])

                forc[t+1] = forc_sens*np.log(np.sum(stockCO2_layers[:,t+1])/S_preind)/np.log(2) + forc_noCO2[t+1]
                #print('forc[t+1]', forc[t+1])

                temp_layers[0,t+1] = np.exp(-1/d1)*temp_layers[0,t] + (c1/d1)*forc[t+1]
                #print('temp_layers[0,t+1]',temp_layers[0,t+1]) #This have a small difference from MatLab.
                temp_layers[1,t+1] = np.exp(-1/d2)*temp_layers[1,t] + (c2/d2)*forc[t+1]
                #print('temp_layers[1,t+1]', temp_layers[1,t+1]) #This also have a small difference from MatLab. 

                temp_global[t+1] = np.sum(temp_layers[:,t+1])
                #print('temp_global[t+1]', temp_global[t+1])

                temp_local[:,t+1] = temp0_local + scaler_temp*(temp_global[t+1]-temp0_global)
                #print('temp_local[:,t+1]', temp_local[:,t+1])

                # Update local temperature
                if ind_clim != 0:
                    temp_local_aux = temp_local[:,t+1]
                    #print('temp_local_aux',temp_local_aux)
                    Delta_temp = temp_local[:,t+1] - temp_local[:,t]
                    #print('Delta_temp', Delta_temp)

                # Update damages on amenities and productivities, equations (2) and (6)
                if ind_clim == 1: # damages on both amenities and productivities
                    if ind_agri == 0:
                        amen[:,t+1] = (1+theta_amen_temp(temp_local_aux)*Delta_temp)*amen[:,t]
                        #print('amen', amen[:,t+1])
                        prod[:,t+1] = (1+theta_prod_temp(temp_local_aux)*Delta_temp)*prod[:,t+1]
                        #print('prod', prod[:,t+1])
                    else:
                        amen[:,t+1] = (1+theta_amen_temp(temp_local_aux,agri_index)*Delta_temp)*amen[:,t]
                        prod[:,t+1] = (1+theta_prod_temp(temp_local_aux,agri_index)*Delta_temp)*prod[:,t+1]
                elif ind_clim == 2: # damages only on amenities
                    if ind_agri == 0:
                        amen[:,t+1] = (1+theta_amen_temp(temp_local_aux)*Delta_temp)*amen[:,t]
                    else:
                        amen[:,t+1] = (1+theta_amen_temp(temp_local_aux,agri_index)*Delta_temp)*amen[:,t]
                elif ind_clim == 3: # damages only on productivities
                    if ind_agri == 0:
                        prod[:,t+1] = (1+theta_prod_temp(temp_local_aux)*Delta_temp)*prod[:,t+1]
                    else:
                        prod[:,t+1] = (1+theta_prod_temp(temp_local_aux,agri_index)*Delta_temp)*prod[:,t+1]
                    amen[:,t+1] = amen[:,t]
                elif ind_clim == 0:  # No damages
                    amen[:,t+1] = amen[:,t]

                # Update global population
                log_realgdp = np.log(realgdp[:,t])
                log_realgdp_w = np.log(realgdp_w[t])
                if ind_exo == 0:
                    net_births[:,t] = natal_fct(log_realgdp, temp_local_aux, log_realgdp_w, coeff_pop)
                    #print('net_births', net_births[:,t])
                    pop_prev = (1+net_births[:,t]) * l[:,t] * H
                    #print('pop_prev', pop_prev)
                    lbar_time[t+1] = round(np.sum(pop_prev))
                    #print('lbar_time', lbar_time[t+1])
    # Sum CO2 stock layers, equation (35)
    stockCO2 = np.sum(stockCO2_layers, axis=0)
                    
    # Assign values to the variables
    l_Warm = l
    u_Warm = u
    prod_Warm = prod
    realgdp_Warm = realgdp
    amen_Warm = amen
    emiCO2_ff_Warm = emiCO2_ff
    emiCO2_total_Warm = emiCO2_total
    stockCO2_Warm = stockCO2
    temp_global_Warm = temp_global
    temp_local_Warm = temp_local
    price_emi_Warm = price_fossil
    clean_Warm = clean
    price_clean_Warm = price_clean
    net_births_Warm = net_births

    return (l_Warm, u_Warm, prod_Warm, realgdp_Warm, amen_Warm, emiCO2_ff_Warm,
            emiCO2_total_Warm, stockCO2_Warm, temp_global_Warm, temp_local_Warm,
            price_emi_Warm, clean_Warm, price_clean_Warm, net_births_Warm)

In [367]:
# Calling the function
l_Warm, u_Warm, prod_Warm, realgdp_Warm, amen_Warm, emiCO2_ff_Warm, emiCO2_total_Warm, stockCO2_Warm, temp_global_Warm, temp_local_Warm, price_emi_Warm, clean_Warm, price_clean_Warm, net_births_Warm = my_function(my_dict)

/var/folders/4y/vcw_zdbs1y1_42cl4fd7t_wc0000gn/T/ipykernel_3083/4260857818.py:149: RuntimeWarning: invalid value encountered in power
  (fossil_share**ϵ*(1+taxCO2[:,t])**(1-ϵ)*price_fossil[:,t]**(1-ϵ) + \
/var/folders/4y/vcw_zdbs1y1_42cl4fd7t_wc0000gn/T/ipykernel_3083/4260857818.py:153: RuntimeWarning: invalid value encountered in power
  (fossil_share**ϵ*(1+taxCO2[:,t])**(-ϵ)*price_fossil[:,t]**(1-ϵ) + \


ValueError: cannot convert float NaN to integer

In [ ]:

# Create a dictionary with desired variable names
data = {
    'l_Warm': l_Warm,
    'u_Warm': u_Warm,
    'prod_Warm': prod_Warm,
    'realgdp_Warm': realgdp_Warm,
    'amen_Warm': amen_Warm,
    'emiCO2_ff_Warm': emiCO2_ff_Warm,
    'emiCO2_total_Warm': emiCO2_total_Warm,
    'stockCO2_Warm': stockCO2_Warm,
    'temp_global_Warm': temp_global_Warm,
    'temp_local_Warm': temp_local_Warm,
    'price_emi_Warm': price_emi_Warm,
    'clean_Warm': clean_Warm,
    'price_clean_Warm': price_clean_Warm,
    'net_births_Warm': net_births_Warm,
}

# Save the variables
save_path = '/Users/jonebo/Documents/BI/Masteroppgave/Code_EGGW/Data/Derived/'
np.savez(save_path + 'results_forward_Warm_EPS01.npz', **data)